In [1]:
%load_ext autoreload
%autoreload 2
%matplotlib inline  

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.offline as pl
pl.init_notebook_mode(connected=True)
import plotly.graph_objs as go

from datetime import datetime, timedelta
import parseIntervalFiles as pif
import parseActivityFiles as paf
#pun intended :)
import consolidateFiles as cf
import datacleaning as cl
import dataviz as dv

In [2]:
verbose = True

PATH = "C:\\Users\\ju\\GDrive\\Projects\\HeRV\\Data\\"
RAW = PATH + "Raw"

In [3]:
file = PATH + "PreProcessed\\sessions.xlsx"
df = pd.read_excel(file)
df.sample(5)

activity  beatscount  duration            hf       hfnu  \
365             eat        1370      1020    290.759649  27.785084   
99   focused-active         147       364    555.705629  63.191638   
129  focused-active        1964      1365    206.852945  28.427889   
427    rest-passive         897       727   1071.803506  61.211322   
190        movement        2153      1184  10572.968418  62.464387   

              lf     lf_hf       lfnu         mhr        mrri   ...     \
365   755.699854  2.599053  72.214916   80.131622  753.950365   ...      
99    323.691776  0.582488  36.808362   73.706616  816.401361   ...      
129   520.787939  2.517672  71.572111   84.806782  711.248982   ...      
427   679.185466  0.633685  38.788678   72.806069  828.516165   ...      
190  6353.425912  0.600912  37.535613  118.484194  539.089178   ...      

     posture removed_artifacts       rmssd        sdnn               start  \
365      sit                 0   26.710170   64.779114 2017-10-26 20:41:00   
99       sit                 0   43.001752   44.723758 2017-10-29 11:58:35   
129      sit                 0   25.072295   51.971333 2017-11-07 20:46:47   
427      sit                 0   65.660671   59.343338 2017-12-27 16:35:46   
190    stand                71  166.900248  158.052090 2018-02-20 18:49:20   

                   stop   total_power user          vlf  sess_id  
365 2017-10-26 20:58:00   1913.218777    2   866.759273      365  
99  2017-10-29 12:04:39   1543.657049    0   664.259643       99  
129 2017-11-07 21:09:32   1443.922259    0   716.281375      129  
427 2017-12-27 16:47:53   2205.909947    5   454.920975      427  
190 2018-02-20 19:09:04  18876.671487    0  1950.277157      190  

[5 rows x 23 columns]

In [4]:
len(df)

450

## Plotting random examples of RR time series for each type of activity

In [7]:
for act in df['activity'].unique():
    v = df[df['activity'] == act].sample(1)
    print('---------------- ', act, ' ---------------')
    for i in range(1):
        print('USER: ', v.iloc[i]['user'])
        dv.plot_sess_rr(v.iloc[i], RAW, act)

----------------  focused-active  ---------------
USER:  0


----------------  leisure  ---------------
USER:  0


----------------  eat  ---------------
USER:  2


----------------  movement  ---------------
USER:  2


----------------  sleep  ---------------
USER:  0


----------------  rest-passive  ---------------
USER:  1


----------------  rest-active  ---------------
USER:  6


----------------  household-chores  ---------------
USER:  0


----------------  focused-passive  ---------------
USER:  2


----------------  exercise  ---------------
USER:  1


### Removing outliers from frequency domain

In [6]:
dfc = df[df['hf'] < 7000]
print(len(df) - len(dfc))
print(len(dfc))

40
410


In [7]:
dfc = dfc[dfc['lf'] < 7000]
print(len(dfc))

409


## Plotting features summary for each type of session
---

In [8]:
for user in range(3):    
    dfu = dfc[dfc['user'] == user]
    print('---------------------------------------- ', user, ' ----------------------------------------')
    for feat in cl.features_all:
        dv.boxplot_compare(dfu, feat, groupby='activity', min_examples=2)

----------------------------------------  0  ----------------------------------------


----------------------------------------  1  ----------------------------------------


----------------------------------------  2  ----------------------------------------


## Plotting features summary for each user
---

In [23]:
ulist = [0,1,2,4,5,6]
alist = ['leisure','focused-passive', 'focused-active','rest-passive','rest-active']
dfv = dfc[(dfc.activity.isin(alist))]
for feat in cl.features_all:
    dv.boxplot_compare(dfv, feat, groupby='user', min_examples=2)

## Assessing how features evolve within a session
---

### Load sessions fragmented in 60 seconds

In [8]:
fdf = pd.read_excel('../data/fragments/df_60_30.xlsx')

In [9]:
fdf.describe()

beatcount            hf          hfnu            lf         lf_hf  \
count  19233.000000  19233.000000  19233.000000  19233.000000  19233.000000   
mean      80.363334   1773.941653     49.715246   1531.153352      2.214625   
std       20.802385   2950.548394     25.388744   2840.047921      3.537051   
min       37.000000      0.077152      0.749662      0.173046      0.005172   
25%       68.000000    225.169651     27.548188    217.729426      0.399618   
50%       77.000000    580.018943     49.822851    596.142299      1.007111   
75%       87.000000   1604.705984     71.448061   1579.597222      2.630003   
max      186.000000  14976.717492     99.485487  38797.808704    132.393456   

               lfnu           mhr          mrri          nn50         order  \
count  19233.000000  19233.000000  19233.000000  19233.000000  19233.000000   
mean      50.284754     80.330579    793.353147     15.412052     90.554724   
std       25.388744     19.158152    168.537135     13.509879    113.640431   
min        0.514513     43.512674    327.907104      0.000000      0.000000   
25%       28.551939     68.751270    694.717647      4.000000     12.000000   
50%       50.177149     77.087860    785.960526     12.000000     36.000000   
75%       72.451812     87.477389    882.623188     24.000000    132.000000   
max       99.250338    183.052548   1382.954545    100.000000    571.000000   

              pnn50         rmssd          sdnn          sess   total_power  \
count  19233.000000  19233.000000  19233.000000  19233.000000  19233.000000   
mean      22.114158     61.525357     70.406003    213.207768   4763.583921   
std       20.560198     52.131322     45.708567    137.217487   6895.635161   
min        0.000000      1.424952      2.100095      0.000000      0.980344   
25%        4.878049     26.782073     38.349954     97.000000    962.270918   
50%       16.438356     42.529168     56.484266    188.000000   2101.509697   
75%       34.375000     79.151921     89.612703    349.000000   5157.723253   
max       94.444444    431.483256    328.385002    446.000000  70185.639553   

               user           vlf  
count  19233.000000  19233.000000  
mean       1.298393   1458.488916  
std        1.902666   3183.156723  
min        0.000000      0.000000  
25%        0.000000    180.706275  
50%        0.000000    514.230086  
75%        2.000000   1428.327446  
max        6.000000  61682.589010

### Helper to choose an activity

In [10]:
df.loc[(df['activity']=='movement') & (df['user']== 1)][['user', 'activity', 'start', 'duration', 'beatscount']].sort_values(by='duration', ascending=False)

user  activity               start  duration  beatscount
238     1  movement 2017-11-02 19:49:37      2178        3614
235     1  movement 2017-11-01 17:02:13      2072        3733
255     1  movement 2017-11-30 15:02:00       942         880
266     1  movement 2018-05-08 10:10:50       905        1961
257     1  movement 2017-11-30 15:50:40       679         994

### Exercise
20 min switch exercise type (aerobic -> strength)

In [11]:
layout = go.Layout( yaxis=dict( title='t (minutos)'))

In [12]:
pp = fdf.loc[fdf['sess'] == 207].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3), layout)

### Movement

In [13]:
pp = fdf.loc[fdf['sess'] == 198].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### Sleeping

In [14]:
pp = fdf.loc[fdf['sess'] == 188].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=5))

### A long session of lectures

In [15]:
pp = fdf.loc[fdf['sess'] == 31].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### A single lecture
148 - lose focus after an hour <br>
107 - keep focus

In [16]:
pp = fdf.loc[fdf['sess'] == 107].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### Work session
seems like a pomodoro break there :)

In [17]:
pp = fdf.loc[fdf['sess'] == 230].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

In [18]:
df.describe()

beatscount      duration            hf        hfnu            lf  \
count    450.000000    450.000000    450.000000  450.000000    450.000000   
mean    3925.582222   3126.822222   2067.095548   41.767744   1693.621250   
std     6502.564990   5742.013922   3777.616059   17.165852   1691.491027   
min      105.000000     88.000000     13.635122    8.241489     36.995074   
25%     1112.000000    900.000000    370.393323   28.610812    673.845680   
50%     1789.000000   1428.000000    719.166158   39.474339   1216.947907   
75%     3771.750000   2458.000000   1606.190331   54.983241   1974.461539   
max    46856.000000  34360.000000  22414.537885   85.318495  12243.363436   

            lf_hf        lfnu         mhr         mrri          nn50  \
count  450.000000  450.000000  450.000000   450.000000    450.000000   
mean     1.955210   58.232256   87.261169   730.931761    932.093333   
std      1.608758   17.165852   19.028288   142.556068   2628.950661   
min      0.172079   14.681505   54.190501   369.893825      0.000000   
25%      0.818736   45.016759   74.684912   642.513222     82.000000   
50%      1.533292   60.525661   83.176087   733.546638    242.500000   
75%      2.495209   71.389188   95.142772   817.104119    530.500000   
max     11.133730   91.758511  164.397688  1144.581425  20895.000000   

            pnn50  removed_artifacts       rmssd        sdnn   total_power  \
count  450.000000         450.000000  450.000000  450.000000    450.000000   
mean    17.414980          24.200000   65.040535   91.059682   5138.145294   
std     15.433927          63.972711   50.889449   43.606087   6162.382931   
min      0.000000           0.000000    5.402758   21.083352    150.076646   
25%      5.880139           0.000000   32.713546   61.912978   1745.794584   
50%     13.670047           1.000000   48.330213   78.514148   3205.454764   
75%     24.888292          14.000000   76.322143  108.261929   5268.507993   
max     81.780538         591.000000  290.138931  253.787250  36726.950587   

             user          vlf     sess_id  
count  450.000000   450.000000  450.000000  
mean     1.280000  1377.428496  224.500000  
std      1.592521  1240.472581  130.048068  
min      0.000000    52.162541    0.000000  
25%      0.000000   570.739610  112.250000  
50%      1.000000  1022.983694  224.500000  
75%      2.000000  1713.661655  336.750000  
max      6.000000  7350.357547  449.000000

In [19]:
df.loc[df['activity'] == 'leisure-active']

Empty DataFrame
Columns: [activity, beatscount, duration, hf, hfnu, lf, lf_hf, lfnu, mhr, mrri, nn50, notes, pnn50, posture, removed_artifacts, rmssd, sdnn, start, stop, total_power, user, vlf, sess_id]
Index: []

[0 rows x 23 columns]

In [20]:
pp = fdf.loc[fdf['sess'] == 440].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))